This is the file corresponding to Problem 2 on the Midterm Exam.

In [1]:
from pyomo.environ import *
from pyomo.opt import *
opt = solvers.SolverFactory("glpk")

In [2]:
t = {'Cut': 38, 'Roll': 28, 'Weld': 21}
p = {'P01': 260, 'P02': 350, 'P03': 250, 'P04': 370}
w = {('Cut', 'P01'): 1.1,
     ('Cut', 'P02'): 2.5,
     ('Cut', 'P03'): 1.7,
     ('Cut', 'P04'): 2.6,
     ('Roll', 'P01'): 1.7,
     ('Roll', 'P02'): 2.1,
     ('Roll', 'P03'): 1.4,
     ('Roll', 'P04'): 2.4,
     ('Weld', 'P01'): 1.6,
     ('Weld', 'P02'): 1.3,
     ('Weld', 'P03'): 1.6,
     ('Weld', 'P04'): 0.8}

P = list(p.keys())
M = list(t.keys())

model = ConcreteModel()
model.x = Var(P, within=NonNegativeReals)

def profit_rule(model):
    return sum(p[j]*model.x[j] for j in P)
model.profit = Objective(rule=profit_rule, sense=maximize)

def capacity_rule(model, i):
    return sum(w[i,j]*model.x[j] for j in P) <= t[i]
model.capacity_constraint = Constraint(M, rule=capacity_rule)

model.dual = Suffix(direction=Suffix.IMPORT)
results = opt.solve(model)

In [3]:
model.x.get_values()

{'P01': 0.0, 'P02': 10.0, 'P03': 5.0, 'P04': 0.0}

In [4]:
model.profit.expr()

4750.0

In [5]:
[(i, 
  model.dual[model.capacity_constraint[i]],
  model.capacity_constraint[i].uslack()) 
 for i in M]

[('Cut', 0.0, 4.5),
 ('Weld', 22.7272727272728, 0.0),
 ('Roll', 152.597402597403, 0.0)]